In [10]:
!pip install pydub mutagen pytaglib

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 193.6/193.6 KB 2.1 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 894.4/894.4 KB 4.0 MB/s eta 0:00:0000:0100:01


In [17]:
from pydub import AudioSegment
from pydub.utils import mediainfo
import taglib
import os

def make_mono(in_file, out_file):
    sound = AudioSegment.from_wav(in_file)
    sound = sound.set_channels(1)
    tags = mediainfo(in_file).get('TAG', {})
    tags['TRACKNUMBER'] = tags['track']
    print(in_file)
    sound.export(out_file, format="wav")
    with taglib.File(out_file, save_on_exit=True) as song:
        song.tags = tags
    print(mediainfo(out_file))

for file in os.listdir('../seth/wavs'):
    make_mono("../seth/wavs/"+file, "../sethmono/wavs/"+file)

../seth/wavs/SK001-0001.wav
{'index': '0', 'codec_name': 'pcm_s16le', 'codec_long_name': 'PCM signed 16-bit little-endian', 'profile': 'unknown', 'codec_type': 'audio', 'codec_tag_string': '[1][0][0][0]', 'codec_tag': '0x0001', 'sample_fmt': 's16', 'sample_rate': '22050', 'channels': '1', 'channel_layout': 'unknown', 'bits_per_sample': '16', 'id': 'N/A', 'r_frame_rate': '0/0', 'avg_frame_rate': '0/0', 'time_base': '1/22050', 'start_pts': 'N/A', 'start_time': 'N/A', 'duration_ts': '169216', 'duration': '7.674195', 'bit_rate': '354171', 'max_bit_rate': 'N/A', 'bits_per_raw_sample': 'N/A', 'nb_frames': 'N/A', 'nb_read_frames': 'N/A', 'nb_read_packets': 'N/A', 'DISPOSITION': {'default': '0', 'dub': '0', 'original': '0', 'comment': '0', 'lyrics': '0', 'karaoke': '0', 'forced': '0', 'hearing_impaired': '0', 'visual_impaired': '0', 'clean_effects': '0', 'attached_pic': '0', 'timed_thumbnails': '0'}, 'filename': '../sethmono/wavs/SK001-0001.wav', 'nb_streams': '1', 'nb_programs': '0', 'format_

In [ ]:
import os

# Trainer: Where the ✨️ happens.
# TrainingArgs: Defines the set of arguments of the Trainer.
from trainer import Trainer, TrainerArgs

# GlowTTSConfig: all model related values for training, validating and testing.
from TTS.tts.configs.vits_config import VitsConfig

# BaseDatasetConfig: defines name, formatter and path of the dataset.
from TTS.tts.configs.shared_configs import BaseDatasetConfig
from TTS.tts.datasets import load_tts_samples
from TTS.tts.models.vits import Vits
from TTS.tts.utils.text.tokenizer import TTSTokenizer
from TTS.utils.audio import AudioProcessor

# we use the same path as this script as our training folder.
output_path = os.path.dirname(os.path.abspath('../../TTS'))

# DEFINE DATASET CONFIG
# Set LJSpeech as our target dataset and define its path.
# You can also use a simple Dict to define the dataset and pass it to your custom formatter.
dataset_config = BaseDatasetConfig(
    formatter="ljspeech", meta_file_train="metadata.csv", path=os.path.join(output_path, "SethVoice/sethmono")
)

# INITIALIZE THE TRAINING CONFIGURATION
# Configure the model. Every config class inherits the BaseTTSConfig.
config = VitsConfig(
    datasets=[dataset_config],
)

# INITIALIZE THE AUDIO PROCESSOR
# Audio processor is used for feature extraction and audio I/O.
# It mainly serves to the dataloader and the training loggers.
ap = AudioProcessor.init_from_config(config)

# INITIALIZE THE TOKENIZER
# Tokenizer is used to convert text to sequences of token IDs.
# If characters are not defined in the config, default characters are passed to the config
tokenizer, config = TTSTokenizer.init_from_config(config)

# LOAD DATA SAMPLES
# Each sample is a list of ```[text, audio_file_path, speaker_name]```
# You can define your custom sample loader returning the list of samples.
# Or define your custom formatter and pass it to the `load_tts_samples`.
# Check `TTS.tts.datasets.load_tts_samples` for more details.
train_samples, eval_samples = load_tts_samples(
    dataset_config,
    eval_split=True,
    eval_split_max_size=config.eval_split_max_size,
    eval_split_size=config.eval_split_size,
)

# INITIALIZE THE MODEL
# Models take a config object and a speaker manager as input
# Config defines the details of the model like the number of layers, the size of the embedding, etc.
# Speaker manager is used by multi-speaker models.
model = Vits(config, ap, tokenizer, speaker_manager=None)

# INITIALIZE THE TRAINER
# Trainer provides a generic API to train all the 🐸TTS models with all its perks like mixed-precision training,
# distributed training, etc.
trainer = Trainer(
    TrainerArgs(), config, output_path, model=model, train_samples=train_samples, eval_samples=eval_samples
)

# AND... 3,2,1... 🚀
trainer.fit()

 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:0
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:None
 | > fft_size:1024
 | > power:None
 | > preemphasis:0.0
 | > griffin_lim_iters:None
 | > signal_norm:None
 | > symmetric_norm:None
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:None
 | > pitch_fmax:None
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:1.0
 | > clip_norm:True
 | > do_trim_silence:False
 | > trim_db:60
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024
 | > Found 585 files in /root/tts-output/SethVoice/sethmono


 > Training Environment:
 | > Backend: Torch
 | > Mixed precision: False
 | > Precision: float32
 | > Current device: 0
 | > Num. of GPUs: 1
 | > Num. of CPUs: 24
 | > Num. of Torch Threads: 12
 | > Torch seed: 54321
 | > Torch CUDNN: True
 | > Torch CUDNN deterministic: False
 | > Torch CUDNN benchmark: False
 | > Torch TF32 MatMul: False
 > Start Tensorboard: tensorboard --logdir=output/run-August-13-2023_06+28PM-0000000

 > Model has 83046892 parameters

 > EPOCH: 0/1000
 --> output/run-August-13-2023_06+28PM-0000000




> DataLoader initialization
| > Tokenizer:
	| > add_blank: True
	| > use_eos_bos: False
	| > use_phonemes: False
| > Number of instances : 580



 > TRAINING (2023-08-13 18:28:42) 


 | > Preprocessing samples
 | > Max text length: 172
 | > Min text length: 21
 | > Avg text length: 99.60689655172413
 | 
 | > Max audio length: 240538.0
 | > Min audio length: 35994.0
 | > Avg audio length: 135175.96379310344
 | > Num. instances discarded samples: 0
 | > Batch group size: 0.
eight. The press yard.

 [!] Character '\n' not found in the vocabulary. Discarding it.


...


  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.03732895851135254 (+0.0)
     | > avg_loss_disc: 2.5519232749938965 (+0.0)
     | > avg_loss_disc_real_0: 0.19538049399852753 (+0.0)
     | > avg_loss_disc_real_1: 0.3046811521053314 (+0.0)
     | > avg_loss_disc_real_2: 0.26399126648902893 (+0.0)
     | > avg_loss_disc_real_3: 0.24605433642864227 (+0.0)
     | > avg_loss_disc_real_4: 0.20383663475513458 (+0.0)
     | > avg_loss_disc_real_5: 0.22820746898651123 (+0.0)
     | > avg_loss_0: 2.5519232749938965 (+0.0)
     | > avg_loss_gen: 2.1831188201904297 (+0.0)
     | > avg_loss_kl: 2.635654926300049 (+0.0)
     | > avg_loss_feat: 3.665600061416626 (+0.0)
     | > avg_loss_mel: 24.406911849975586 (+0.0)
     | > avg_loss_duration: 1.7388668060302734 (+0.0)
     | > avg_loss_1: 34.630157470703125 (+0.0)


 > EPOCH: 662/1000
 --> output/run-August-13-2023_06+28PM-0000000

 > TRAINING (2023-08-14 00:00:51) 

 > EVALUATION 


  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.03799533843

 | > Synthesizing test sentences.



  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.037995338439941406 (+0.0)
     | > avg_loss_disc: 2.3763418197631836 (+0.0)
     | > avg_loss_disc_real_0: 0.27706870436668396 (+0.0)
     | > avg_loss_disc_real_1: 0.22504596412181854 (+0.0)
     | > avg_loss_disc_real_2: 0.1612960547208786 (+0.0)
     | > avg_loss_disc_real_3: 0.20384618639945984 (+0.0)
     | > avg_loss_disc_real_4: 0.17418219149112701 (+0.0)
     | > avg_loss_disc_real_5: 0.20545491576194763 (+0.0)
     | > avg_loss_0: 2.3763418197631836 (+0.0)
     | > avg_loss_gen: 2.3076610565185547 (+0.0)
     | > avg_loss_kl: 2.573829174041748 (+0.0)
     | > avg_loss_feat: 4.195895671844482 (+0.0)
     | > avg_loss_mel: 24.3289794921875 (+0.0)
     | > avg_loss_duration: 1.7541773319244385 (+0.0)
     | > avg_loss_1: 35.16054153442383 (+0.0)


 > EPOCH: 663/1000
 --> output/run-August-13-2023_06+28PM-0000000

 > TRAINING (2023-08-14 00:01:21) 

   --> TIME: 2023-08-14 00:01:26 -- STEP: 3/19 -- GLOBAL_STEP: 12600
     | > los

 | > Synthesizing test sentences.



  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.043226003646850586 (+0.0)
     | > avg_loss_disc: 2.602734088897705 (+0.0)
     | > avg_loss_disc_real_0: 0.13098031282424927 (+0.0)
     | > avg_loss_disc_real_1: 0.26720061898231506 (+0.0)
     | > avg_loss_disc_real_2: 0.22940702736377716 (+0.0)
     | > avg_loss_disc_real_3: 0.2265123873949051 (+0.0)
     | > avg_loss_disc_real_4: 0.274046927690506 (+0.0)
     | > avg_loss_disc_real_5: 0.25379523634910583 (+0.0)
     | > avg_loss_0: 2.602734088897705 (+0.0)
     | > avg_loss_gen: 2.018791913986206 (+0.0)
     | > avg_loss_kl: 2.856525421142578 (+0.0)
     | > avg_loss_feat: 3.470693826675415 (+0.0)
     | > avg_loss_mel: 23.20816421508789 (+0.0)
     | > avg_loss_duration: 1.7344342470169067 (+0.0)
     | > avg_loss_1: 33.28860855102539 (+0.0)


 > EPOCH: 664/1000
 --> output/run-August-13-2023_06+28PM-0000000

 > TRAINING (2023-08-14 00:01:50) 
 > Keyboard interrupt detected.
 > Saving model before exiting...

 > CHECKPOINT : out

In [13]:
import os
os.path.exists('/root/tts-output/SethVoice/TTS/output/run-August-13-2023_06+28PM-0000000/config.json')

True

In [4]:
from TTS.api import Synthesizer

tts = Synthesizer(tts_checkpoint="../TTS/output/run-August-13-2023_06+28PM-0000000/best_model_11229.pth", tts_config_path="../TTS/output/run-August-13-2023_06+28PM-0000000/config.json")

#tts = TTS(model_name="/root/tts-output/run-July-26-2023_12+16AM-0000000/best_model_1908.pth", progress_bar=True, gpu=True)

 > Using model: vits
 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:0
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:None
 | > fft_size:1024
 | > power:None
 | > preemphasis:0.0
 | > griffin_lim_iters:None
 | > signal_norm:None
 | > symmetric_norm:None
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:None
 | > pitch_fmax:None
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:1.0
 | > clip_norm:True
 | > do_trim_silence:False
 | > trim_db:60
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024


In [8]:
outputs = tts.tts(text="I will beat you all at fantasy football.")
tts.save_wav(outputs, "output.wav")

 > Text splitted to sentences.
['I will beat you all at fantasy football.']
 > Processing time: 0.558802604675293
 > Real-time factor: 0.17822259652120764


In [ ]:
import os

from trainer import Trainer, TrainerArgs

from TTS.utils.audio import AudioProcessor
from TTS.vocoder.configs import HifiganConfig
from TTS.vocoder.datasets.preprocess import load_wav_data
from TTS.vocoder.models.gan import GAN

# we use the same path as this script as our training folder.
output_path = os.path.dirname(os.path.abspath('../../TTS'))

config = HifiganConfig(
    batch_size=32,
    eval_batch_size=16,
    num_loader_workers=4,
    num_eval_loader_workers=4,
    run_eval=True,
    test_delay_epochs=5,
    epochs=1000,
    seq_len=8192,
    pad_short=2000,
    use_noise_augment=True,
    eval_split_size=10,
    print_step=25,
    print_eval=False,
    mixed_precision=False,
    lr_gen=1e-4,
    lr_disc=1e-4,
    data_path= os.path.join(output_path, "SethVoice/sethmono/wavs"),
    output_path=output_path,
)

# init audio processor
ap = AudioProcessor(**config.audio.to_dict())

# load training samples
eval_samples, train_samples = load_wav_data(config.data_path, config.eval_split_size)

# init model
model = GAN(config, ap)

# init the trainer and 🚀
trainer = Trainer(
    TrainerArgs(), config, output_path, model=model, train_samples=train_samples, eval_samples=eval_samples
)
trainer.fit()

 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:-100
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:20
 | > fft_size:1024
 | > power:1.5
 | > preemphasis:0.0
 | > griffin_lim_iters:60
 | > signal_norm:True
 | > symmetric_norm:True
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:1.0
 | > pitch_fmax:640.0
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:4.0
 | > clip_norm:True
 | > do_trim_silence:True
 | > trim_db:45
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024
 > Generator Model: hifigan_generator
 > Discriminator Model: hifigan_discriminator


 > Training Environment:
 | > Backend: Torch
 | > Mixed precision: False
 | > Precision: float32
 | > Current device: 0
 | > Num. of GPUs: 1
 | > Num. of CPUs: 24
 | > Num. of Torch Threads: 12
 | > Torch seed: 54321
 | > Torch CUDNN: True
 | > Torch CUDNN deterministic: False
 | > Torch CUDNN benchmark: False
 | > Torch TF32 MatMul: False
 > Start Tensorboard: tensorboard --logdir=/root/tts-output/run-August-14-2023_12+09AM-0000000

 > Model has 84660721 parameters

 > EPOCH: 0/1000
 --> /root/tts-output/run-August-14-2023_12+09AM-0000000

 > TRAINING (2023-08-14 00:09:46) 
/usr/local/lib/python3.10/dist-packages/torch/nn/modules/conv.py:309: UserWarning: Applied workaround for CuDNN issue, install nvrtc.so (Triggered internally at ../aten/src/ATen/native/cudnn/Conv_v8.cpp:80.)
  return F.conv1d(input, weight, bias, self.stride,
/usr/local/lib/python3.10/dist-packages/torch/functional.py:641: UserWarning: stft with return_complex=False is deprecated. In a future pytorch release, stft 

In [3]:
# Vocoder not needed and does not work with VITS model
from TTS.api import Synthesizer

tts = Synthesizer(tts_checkpoint="../TTS/output/run-August-13-2023_06+28PM-0000000/best_model_11229.pth",
                  tts_config_path="../TTS/output/run-August-13-2023_06+28PM-0000000/config.json",
                  vocoder_checkpoint="../../run-August-14-2023_12+09AM-0000000/best_model_486.pth",
                  vocoder_config="../../run-August-14-2023_12+09AM-0000000/config.json"
                 )

#tts = TTS(model_name="/root/tts-output/run-July-26-2023_12+16AM-0000000/best_model_1908.pth", progress_bar=True, gpu=True)

outputs = tts.tts(text="Hello mother. I am Seth's voice clone.")
tts.save_wav(outputs, "output.wav")

 > Using model: vits
 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:0
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:None
 | > fft_size:1024
 | > power:None
 | > preemphasis:0.0
 | > griffin_lim_iters:None
 | > signal_norm:None
 | > symmetric_norm:None
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:None
 | > pitch_fmax:None
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:1.0
 | > clip_norm:True
 | > do_trim_silence:False
 | > trim_db:60
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024
 > Vocoder Model: hifigan
 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:-100
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:

RuntimeError: Given groups=1, weight of size [512, 80, 7], expected input[1, 47872, 11] to have 80 channels, but got 47872 channels instead